In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import scipy.stats as stats
import statsmodels.api as sm
import regex as re
import plotly.express as px
import requests
from bs4 import BeautifulSoup as BS
from io import StringIO
import statsmodels
%matplotlib inline

In [2]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)

#### Define payload parameters

In [65]:
payload = {'format' :'csv',
          'starttime':'1900-01-01',
          'minlatitude':'34.964513',
          'maxlatitude':'36.723245',
          'minlongitude':'-90.282394',
          'maxlongitude':'-81.647141',
          'orderby':'time'}
#,'limit':'200000'

#### Check number of records with 'count' method

In [66]:
records_count = 'https://earthquake.usgs.gov/fdsnws/event/1/count?'

In [67]:
r = requests.get(url=records_count, params=payload)

In [68]:
print(requests.get(url=records_count, params=payload).text)

9233


### Run query & read in results to dataframe

In [69]:
query = 'https://earthquake.usgs.gov/fdsnws/event/1/query?'

In [70]:
r = requests.get(url=query, params=payload)

In [71]:
print(r)

<Response [200]>


In [72]:
usgs = pd.read_csv(StringIO(r.text))

In [73]:
pd.set_option('display.max_columns', 50)
pd.set_option('display.max_rows', 100)

In [7]:
usgs_tn=pd.read_csv('../data/usgs_tn_earthquakes.csv')
usgs_tn.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4764 entries, 0 to 4763
Data columns (total 11 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   time            4764 non-null   object 
 1   depth           4764 non-null   float64
 2   mag             4764 non-null   float64
 3   mag_type        4764 non-null   object 
 4   place           4764 non-null   object 
 5   latitude        4764 non-null   float64
 6   longitude       4764 non-null   float64
 7   type            4764 non-null   object 
 8   id              4764 non-null   object 
 9   mag_bins_whole  4764 non-null   object 
 10  mag_bins_half   4764 non-null   object 
dtypes: float64(4), object(7)
memory usage: 409.5+ KB


### (Re)Format the data
Datetime did not save in CSV export. Also, Plotly animations don't seem to like dt types (investigate why) and want string

In [8]:
usgs_tn['time']=pd.to_datetime(usgs_tn['time']).dt.floor('D')

In [ ]:
usgs_tn['year']=usgs_tn['time'].dt.year

In [ ]:
usgs_tn['time']=usgs_tn['time'].astype(str)

In [38]:
usgs_tn.time[1]

#### Parse the magnitude values into bins
bin values have changed datatypes. Drop columns and re-assign bin values properly.

In [12]:
#Check dtype of bins --> back to a string value.
usgs_tn.mag_bins_half.dtype

dtype('O')

In [14]:
usgs_tn = usgs_tn.drop(columns=['mag_bins_whole','mag_bins_half'])

In [15]:
#Binning magnitude by whole number intervals
mag_labels_whole = ['-0.50-0.99', '1.0-1.99', '2.0-2.99', '3.0-3.99','4.0-4.99', '5.0-5.99', '6.0-6.99']
mag_cut_whole = [-0.5, 0.99, 1.99, 2.99, 3.99, 4.99, 5.99, 6.99]
usgs_tn['mag_bins_whole'] = pd.cut(usgs_tn['mag'], bins=mag_cut_whole, labels=mag_labels_whole)#.value_counts()

In [16]:
#Binning magnitude by intervals of .5
mag_labels_half = ['0-0.49', '0.50-0.99', '1.0-1.49', '1.50-1.99','2.0-2.49', '2.5-2.99', '3.0-3.49','3.5-3.99','4.0-4.49', '4.5-4.99','5.0-5.49', '5.5-5.99','6.0-6.49','6.5-7']
mag_cut_half = [-0.5, 0.49, 0.99, 1.49, 1.99, 2.49, 2.99, 3.49, 3.99, 4.49, 4.99, 5.49, 5.99, 6.49, 6.99]
usgs_tn['mag_bins_half'] = pd.cut(usgs_tn['mag'], bins=mag_cut_half, labels=mag_labels_half)#.value_counts()

In [18]:
#double check dtype of bins --> looks correct now
usgs_tn.mag_bins_half.dtype

CategoricalDtype(categories=['0-0.49', '0.50-0.99', '1.0-1.49', '1.50-1.99', '2.0-2.49',
                  '2.5-2.99', '3.0-3.49', '3.5-3.99', '4.0-4.49', '4.5-4.99',
                  '5.0-5.49', '5.5-5.99', '6.0-6.49', '6.5-7'],
                 ordered=True)

### Poisson Distribution

What is the probability that the next earthquake of X magnitude would hit TN within Y time period?
Because dataset only contains earthquakes up to 4.5, calculations return a zero probability of anything over 4.5. 

**NOT reliable probability calculation**.  Also...too many other factors. This is merely relying on time and past recorded events. 

In [22]:
usgs_tn.mag_bins_whole.value_counts()

1.0-1.99      3455
2.0-2.99       991
-0.50-0.99     231
3.0-3.99        77
4.0-4.99        10
6.0-6.99         0
5.0-5.99         0
Name: mag_bins_whole, dtype: int64

In [23]:
#Find number of earthquake events 4.0 or greater
usgs_tn[usgs_tn['mag']>3.99]['mag'].count()

10

In [24]:
#Find the time span of earthquake records - default to 1928-2020
observed_dates = (usgs_tn.time.max() - usgs_tn.time.min()).days/365
observed_dates

92.07397260273973

In [29]:
#rate of earthquake of given magnitude
rate = (usgs_tn[usgs_tn['mag']>5.0]['mag'].count())/observed_dates
rate

0.0

In [30]:
span = 10
x=0
p=((np.exp(-span*rate))*(span*rate)**x)

print(p,(1-p))

1.0 0.0


### Density mapbox plot
Scale is function of both magnitude AND frequency --> not optimal

In [49]:

df=usgs_tn

fig = px.density_mapbox(df, lat='latitude', lon='longitude', z='mag', radius=5, 
                        #center=dict(lat=0, lon=180),
                        mapbox_style="stamen-toner")
fig.show()

### Animated map of earthquakes in TN from 1928-2020
Write to HTML for presentation in separate tab

Issue - magnitude scale changes with each frame. 

In [51]:
df=usgs_tn.sort_values(by='time',ascending=True)
fig = px.density_mapbox(df, lat='latitude',
                        lon='longitude', 
                        z='mag', 
                        radius=10,
                        mapbox_style="stamen-terrain", 
                        animation_frame="year")

fig.update_layout(mapbox_style="stamen-terrain", mapbox_zoom=5, mapbox_center = {"lat": 35.9917, "lon": -86.3364},)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

fig.layout.updatemenus[0].buttons[0].args[1]["frame"]["duration"] = 600
fig.layout.updatemenus[0].buttons[0].args[1]["transition"]["duration"] = 600
fig.layout.coloraxis.showscale = True   
fig.layout.sliders[0].pad.t = 10
fig.layout.updatemenus[0].pad.t= 10             

fig.show()
fig.write_html("../data/tn_earthquake_density_mapbox.html")

#### Try to resolve color scale issue with a scatter mapbox animation
-Doesn't really work
- **Concerning** : not all the points seem to appear on the plot as the frames go through each year.  Eg: 1983 had over 25 earthquakes.  Likely a function of either the animation settings or how the plot is accessing the earthquake values by year...subject for follow-up

In [153]:
#df=usgs.sort_values(by=['time','mag_bins_half'], ascending = [True,True])
df=usgs.sort_values(by='year', ascending = True)
fig = px.scatter_mapbox(df, lat='latitude', lon='longitude', color='mag_bins_whole', 
                        animation_frame="year", animation_group="time",
                        size="mag",
                color_discrete_sequence= px.colors.sequential.Plasma,
                        hover_name="place", hover_data=usgs,zoom=3, height=700)
fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

### Earthquake patterns in East vs West TN

In [53]:
df=usgs_tn  #usgs['mag']>=2.0]#[usgs['mag_bins_half'].isin(mag_bins_threshold)]
fig = px.density_mapbox(df, lat='latitude',
                        lon='longitude', 
                        z='mag', 
                        radius=10,
                        mapbox_style="stamen-toner", 
                        title='Density of Earthquakes in East & West TN')

fig.update_layout(mapbox_style="open-street-map", mapbox_zoom=5, mapbox_center = {"lat": 35.9917, "lon": -86.3364},)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
       
fig.show()

#### Static scatterplot

In [54]:
df=usgs.sort_values(by=['time','mag_bins_half'], ascending = [True,True])
fig = px.scatter_mapbox(df, lat='latitude', lon='longitude', #color='mag_bins_whole', 
                        size="mag",
                color_discrete_sequence= px.colors.sequential.Plasma,
                        hover_name="place", hover_data=usgs,zoom=3, height=700)
fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()